**Realizando a conexão com o MongoDB**

In [1]:
from pymongo.mongo_client import MongoClient
from pymongo.server_api import ServerApi
from dotenv import load_dotenv
import os

load_dotenv()

uri = os.getenv("MONGODB_URI")
# Create a new client and connect to the server
client = MongoClient(uri, server_api=ServerApi('1'))
# Send a ping to confirm a successful connection
try:
    client.admin.command('ping')
    print("Pinged your deployment. You successfully connected to MongoDB!")
except Exception as e:
    print(e)

Pinged your deployment. You successfully connected to MongoDB!


## Lendo os dados no MongoDB

In [2]:
client.list_database_names()

['db_produtos', 'admin', 'local']

In [3]:
db = client["db_produtos"]
db.list_collection_names()

['produtos']

In [4]:
collection = db["produtos"]

In [5]:
for doc in collection.find():
    print(doc)

{'_id': ObjectId('65ed49609983749bdcb11ee3'), 'Produto': 'Modelagem preditiva', 'Categoria do Produto': 'livros', 'Preço': 92.45, 'Frete': 5.6096965236, 'Data da Compra': '01/01/2020', 'Vendedor': 'Thiago Silva', 'Local da compra': 'BA', 'Avaliação da compra': 1, 'Tipo de pagamento': 'cartao_credito', 'Quantidade de parcelas': 3, 'lat': -13.29, 'lon': -41.71}
{'_id': ObjectId('65ed49609983749bdcb11ee4'), 'Produto': 'Iniciando em programação', 'Categoria do Produto': 'livros', 'Preço': 43.84, 'Frete': 0.0, 'Data da Compra': '01/01/2020', 'Vendedor': 'Mariana Ferreira', 'Local da compra': 'SP', 'Avaliação da compra': 5, 'Tipo de pagamento': 'cartao_credito', 'Quantidade de parcelas': 1, 'lat': -22.19, 'lon': -48.79}
{'_id': ObjectId('65ed49609983749bdcb11ee5'), 'Produto': 'Pandeiro', 'Categoria do Produto': 'instrumentos musicais', 'Preço': 87.18, 'Frete': 2.2265117938, 'Data da Compra': '01/01/2020', 'Vendedor': 'Thiago Silva', 'Local da compra': 'RJ', 'Avaliação da compra': 4, 'Tipo de

**Alterando os nomes dos campos de latitude e longitude**

In [6]:
collection.update_many({}, {"$rename": {"lat": "Latitude", "lon": "Longitude"}})

UpdateResult({'n': 9435, 'electionId': ObjectId('7fffffff000000000000031a'), 'opTime': {'ts': Timestamp(1710049656, 2217), 't': 794}, 'nModified': 9435, 'ok': 1.0, '$clusterTime': {'clusterTime': Timestamp(1710049656, 2218), 'signature': {'hash': b'\x87\xec@\xa8\xab%0\x01K\x12\x9c2\x1a\x15\xfd\x05\xdc\xca\xc5\xb8', 'keyId': 7298821372183052290}}, 'operationTime': Timestamp(1710049656, 2217), 'updatedExisting': True}, acknowledged=True)

In [7]:
# Vendo que os campos dos documentos foram alterados percorrendo os documentos com a função find(filtro)
for document in collection.find({"Longitude": -48.79}):
    print(document)

{'_id': ObjectId('65ed49609983749bdcb11ee4'), 'Produto': 'Iniciando em programação', 'Categoria do Produto': 'livros', 'Preço': 43.84, 'Frete': 0.0, 'Data da Compra': '01/01/2020', 'Vendedor': 'Mariana Ferreira', 'Local da compra': 'SP', 'Avaliação da compra': 5, 'Tipo de pagamento': 'cartao_credito', 'Quantidade de parcelas': 1, 'Latitude': -22.19, 'Longitude': -48.79}
{'_id': ObjectId('65ed49609983749bdcb11ee8'), 'Produto': 'Jogo de copos', 'Categoria do Produto': 'utilidades domesticas', 'Preço': 54.67, 'Frete': 9.2906273957, 'Data da Compra': '01/01/2020', 'Vendedor': 'Camila Ribeiro', 'Local da compra': 'SP', 'Avaliação da compra': 4, 'Tipo de pagamento': 'boleto', 'Quantidade de parcelas': 1, 'Latitude': -22.19, 'Longitude': -48.79}
{'_id': ObjectId('65ed49609983749bdcb11eeb'), 'Produto': 'Xadrez de madeira', 'Categoria do Produto': 'brinquedos', 'Preço': 25.87, 'Frete': 1.9086041977, 'Data da Compra': '01/01/2020', 'Vendedor': 'Juliana Costa', 'Local da compra': 'SP', 'Avaliação

## Aplicando transformações: filtrando registros da categoria livros

Agora, vamos executar uma consulta para obter apenas os dados relacionados à categoria de **livros**.

In [8]:
collection.distinct("Categoria do Produto")

['brinquedos',
 'eletrodomesticos',
 'eletronicos',
 'esporte e lazer',
 'instrumentos musicais',
 'livros',
 'moveis',
 'utilidades domesticas']

In [9]:
query = {"Categoria do Produto": "livros"}
lista_livros = []

for documents in collection.find(query):
    # print(documents["Vendedor"]) Como documentos "estão em formato json", é possível acessar chaves e valores específicos
    # print(documents)
    lista_livros.append(documents)

In [10]:
lista_livros[0]["Vendedor"]

'Thiago Silva'

**Salvando os dados em um DataFrame**

In [11]:
import pandas as pd
import numpy as np

In [12]:
df_livros = pd.DataFrame(lista_livros)
df_livros

_id                      Produto  \
0    65ed49609983749bdcb11ee3          Modelagem preditiva   
1    65ed49609983749bdcb11ee4     Iniciando em programação   
2    65ed49609983749bdcb11ef6     Iniciando em programação   
3    65ed49609983749bdcb11f04  Ciência de dados com python   
4    65ed49609983749bdcb11f06  Ciência de dados com python   
..                        ...                          ...   
737  65ed49609983749bdcb1437e      Dashboards com Power BI   
738  65ed49609983749bdcb14382  Ciência de dados com python   
739  65ed49609983749bdcb14388          Modelagem preditiva   
740  65ed49609983749bdcb14394          Modelagem preditiva   
741  65ed49609983749bdcb143ba      Dashboards com Power BI   

    Categoria do Produto   Preço     Frete Data da Compra          Vendedor  \
0                 livros   92.45  5.609697     01/01/2020      Thiago Silva   
1                 livros   43.84  0.000000     01/01/2020  Mariana Ferreira   
2                 livros   63.25  3.894137     01/01/2022     Juliana Costa   
3                 livros   86.13  5.273176     01/02/2021    Camila Ribeiro   
4                 livros   72.75  1.458158     01/02/2021    Beatriz Moraes   
..                   ...     ...       ...            ...               ...   
737               livros   41.27  2.728608     31/07/2022        João Souza   
738               livros   81.58  4.632666     31/08/2020     Juliana Costa   
739               livros  109.17  6.701389     31/08/2021     Felipe Santos   
740               livros   94.89  5.578872     31/08/2022       Pedro Gomes   
741               livros   54.85  3.451702     31/12/2022    Lucas Oliveira   

    Local da compra  Avaliação da compra Tipo de pagamento  \
0                BA                    1    cartao_credito   
1                SP                    5    cartao_credito   
2                RJ                    5    cartao_credito   
3                RJ                    4    cartao_credito   
4                PR                    4    cartao_credito   
..              ...                  ...               ...   
737              SC                    5    cartao_credito   
738              SP                    5    cartao_credito   
739              MG                    3    cartao_credito   
740              SP                    5    cartao_credito   
741              RJ                    5    cartao_credito   

     Quantidade de parcelas  Latitude  Longitude  
0                         3    -13.29     -41.71  
1                         1    -22.19     -48.79  
2                         4    -22.25     -42.66  
3                         3    -22.25     -42.66  
4                         2    -24.89     -51.55  
..                      ...       ...        ...  
737                      12    -27.45     -50.95  
738                       2    -22.19     -48.79  
739                       3    -18.10     -44.38  
740                       1    -22.19     -48.79  
741                       3    -22.25     -42.66  

[742 rows x 13 columns]

In [13]:
df_livros.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 742 entries, 0 to 741
Data columns (total 13 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   _id                     742 non-null    object 
 1   Produto                 742 non-null    object 
 2   Categoria do Produto    742 non-null    object 
 3   Preço                   742 non-null    float64
 4   Frete                   742 non-null    float64
 5   Data da Compra          742 non-null    object 
 6   Vendedor                742 non-null    object 
 7   Local da compra         742 non-null    object 
 8   Avaliação da compra     742 non-null    int64  
 9   Tipo de pagamento       742 non-null    object 
 10  Quantidade de parcelas  742 non-null    int64  
 11  Latitude                742 non-null    float64
 12  Longitude               742 non-null    float64
dtypes: float64(4), int64(2), object(7)
memory usage: 75.5+ KB


## Formatando as datas

Para adicionar dados do tipo DATE em um banco de dados MySQL, é necessário que a data esteja no formato **%Y-%m-%d (ano-mês-dia)**. Portanto, realizaremos uma transformação na coluna "Data de Compra" para ajustá-la a esse formato. Dessa forma, poderemos armazenar corretamente as datas no banco de dados MySQL, garantindo consistência e facilitando consultas baseadas em datas posteriormente.

In [14]:
df_livros["Data da Compra"] = pd.to_datetime(df_livros["Data da Compra"], format="%d/%m/%Y")

In [15]:
df_livros.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 742 entries, 0 to 741
Data columns (total 13 columns):
 #   Column                  Non-Null Count  Dtype         
---  ------                  --------------  -----         
 0   _id                     742 non-null    object        
 1   Produto                 742 non-null    object        
 2   Categoria do Produto    742 non-null    object        
 3   Preço                   742 non-null    float64       
 4   Frete                   742 non-null    float64       
 5   Data da Compra          742 non-null    datetime64[ns]
 6   Vendedor                742 non-null    object        
 7   Local da compra         742 non-null    object        
 8   Avaliação da compra     742 non-null    int64         
 9   Tipo de pagamento       742 non-null    object        
 10  Quantidade de parcelas  742 non-null    int64         
 11  Latitude                742 non-null    float64       
 12  Longitude               742 non-null    float64   

**Salvando os dados num arqivo csv**

In [16]:
from pathlib import Path

curdir = Path.cwd()
curdir

PosixPath('/root/Data_Engineering/pipeline-python-mongo-mysql/notebooks')

In [17]:
csv_path = "../csv_files/"

In [18]:
df_livros.to_csv(csv_path + "livros.csv", index=False)

## Aplicando transformações: filtrando produtos vendidos a partir de 2021

Nesta etapa, faremos uma query para selecionar apenas os produtos vendidos a partir do ano de 2021. Utilizaremos um filtro na coluna de data de compra para obter os registros que atendam a essa condição.

In [19]:
collection.find_one()

{'_id': ObjectId('65ed49609983749bdcb11ee3'),
 'Produto': 'Modelagem preditiva',
 'Categoria do Produto': 'livros',
 'Preço': 92.45,
 'Frete': 5.6096965236,
 'Data da Compra': '01/01/2020',
 'Vendedor': 'Thiago Silva',
 'Local da compra': 'BA',
 'Avaliação da compra': 1,
 'Tipo de pagamento': 'cartao_credito',
 'Quantidade de parcelas': 3,
 'Latitude': -13.29,
 'Longitude': -41.71}

In [20]:
query_2 = {"Data da Compra": {"$regex": "/202[1-9]"}}

In [21]:
lista_produtos_2021_diante = []
for doc in collection.find(query_2):
    # print(doc["Data da Compra"])
    lista_produtos_2021_diante.append(doc)

In [22]:
lista_produtos_2021_diante

[{'_id': ObjectId('65ed49609983749bdcb11eec'),
  'Produto': 'Xadrez de madeira',
  'Categoria do Produto': 'brinquedos',
  'Preço': 25.23,
  'Frete': 0.0,
  'Data da Compra': '01/01/2021',
  'Vendedor': 'Thiago Silva',
  'Local da compra': 'BA',
  'Avaliação da compra': 5,
  'Tipo de pagamento': 'cartao_credito',
  'Quantidade de parcelas': 2,
  'Latitude': -13.29,
  'Longitude': -41.71},
 {'_id': ObjectId('65ed49609983749bdcb11eed'),
  'Produto': 'Impressora',
  'Categoria do Produto': 'eletronicos',
  'Preço': 322.04,
  'Frete': 14.7321002401,
  'Data da Compra': '01/01/2021',
  'Vendedor': 'João Souza',
  'Local da compra': 'SP',
  'Avaliação da compra': 3,
  'Tipo de pagamento': 'cartao_credito',
  'Quantidade de parcelas': 1,
  'Latitude': -22.19,
  'Longitude': -48.79},
 {'_id': ObjectId('65ed49609983749bdcb11eee'),
  'Produto': 'Mesa de centro',
  'Categoria do Produto': 'moveis',
  'Preço': 282.22,
  'Frete': 12.6118050347,
  'Data da Compra': '01/01/2021',
  'Vendedor': 'João 

In [23]:
import pandas as pd
import numpy as np

In [24]:
df_produtos = pd.DataFrame(lista_produtos_2021_diante)
df_produtos

_id                  Produto  \
0     65ed49609983749bdcb11eec        Xadrez de madeira   
1     65ed49609983749bdcb11eed               Impressora   
2     65ed49609983749bdcb11eee           Mesa de centro   
3     65ed49609983749bdcb11eef              Tablet ABXY   
4     65ed49609983749bdcb11ef0                    Fogão   
...                        ...                      ...   
6569  65ed49609983749bdcb143b9               Impressora   
6570  65ed49609983749bdcb143ba  Dashboards com Power BI   
6571  65ed49609983749bdcb143bb          Cubo mágico 8x8   
6572  65ed49609983749bdcb143bc                 Faqueiro   
6573  65ed49609983749bdcb143bd              Micro-ondas   

       Categoria do Produto    Preço      Frete Data da Compra  \
0                brinquedos    25.23   0.000000     01/01/2021   
1               eletronicos   322.04  14.732100     01/01/2021   
2                    moveis   282.22  12.611805     01/01/2021   
3               eletronicos  1100.42  68.451348     01/01/2021   
4          eletrodomesticos   791.81  42.444626     01/01/2021   
...                     ...      ...        ...            ...   
6569            eletronicos   472.77  25.456706     31/12/2022   
6570                 livros    54.85   3.451702     31/12/2022   
6571             brinquedos    19.74   0.000000     31/12/2022   
6572  utilidades domesticas    52.49   0.000000     31/12/2022   
6573       eletrodomesticos   711.30  35.459024     31/12/2022   

            Vendedor Local da compra  Avaliação da compra Tipo de pagamento  \
0       Thiago Silva              BA                    5    cartao_credito   
1         João Souza              SP                    3    cartao_credito   
2         João Souza              SP                    3            boleto   
3     Beatriz Moraes              SP                    1             cupom   
4      Juliana Costa              SP                    4            boleto   
...              ...             ...                  ...               ...   
6569  Camila Ribeiro              MT                    4    cartao_credito   
6570  Lucas Oliveira              RJ                    5    cartao_credito   
6571   Bianca Santos              RJ                    5    cartao_credito   
6572   Larissa Alves              DF                    4    cartao_credito   
6573   Bianca Santos              MA                    5    cartao_credito   

      Quantidade de parcelas  Latitude  Longitude  
0                          2    -13.29     -41.71  
1                          1    -22.19     -48.79  
2                          1    -22.19     -48.79  
3                          1    -22.19     -48.79  
4                          1    -22.19     -48.79  
...                      ...       ...        ...  
6569                       3    -12.64     -55.42  
6570                       3    -22.25     -42.66  
6571                       8    -22.25     -42.66  
6572                       5    -15.83     -47.86  
6573                       4     -5.42     -45.44  

[6574 rows x 13 columns]

**Formatando as datas**

In [25]:
df_produtos["Data da Compra"] = pd.to_datetime(df_produtos["Data da Compra"], format="%d/%m/%Y")

In [26]:
df_produtos

_id                  Produto  \
0     65ed49609983749bdcb11eec        Xadrez de madeira   
1     65ed49609983749bdcb11eed               Impressora   
2     65ed49609983749bdcb11eee           Mesa de centro   
3     65ed49609983749bdcb11eef              Tablet ABXY   
4     65ed49609983749bdcb11ef0                    Fogão   
...                        ...                      ...   
6569  65ed49609983749bdcb143b9               Impressora   
6570  65ed49609983749bdcb143ba  Dashboards com Power BI   
6571  65ed49609983749bdcb143bb          Cubo mágico 8x8   
6572  65ed49609983749bdcb143bc                 Faqueiro   
6573  65ed49609983749bdcb143bd              Micro-ondas   

       Categoria do Produto    Preço      Frete Data da Compra  \
0                brinquedos    25.23   0.000000     2021-01-01   
1               eletronicos   322.04  14.732100     2021-01-01   
2                    moveis   282.22  12.611805     2021-01-01   
3               eletronicos  1100.42  68.451348     2021-01-01   
4          eletrodomesticos   791.81  42.444626     2021-01-01   
...                     ...      ...        ...            ...   
6569            eletronicos   472.77  25.456706     2022-12-31   
6570                 livros    54.85   3.451702     2022-12-31   
6571             brinquedos    19.74   0.000000     2022-12-31   
6572  utilidades domesticas    52.49   0.000000     2022-12-31   
6573       eletrodomesticos   711.30  35.459024     2022-12-31   

            Vendedor Local da compra  Avaliação da compra Tipo de pagamento  \
0       Thiago Silva              BA                    5    cartao_credito   
1         João Souza              SP                    3    cartao_credito   
2         João Souza              SP                    3            boleto   
3     Beatriz Moraes              SP                    1             cupom   
4      Juliana Costa              SP                    4            boleto   
...              ...             ...                  ...               ...   
6569  Camila Ribeiro              MT                    4    cartao_credito   
6570  Lucas Oliveira              RJ                    5    cartao_credito   
6571   Bianca Santos              RJ                    5    cartao_credito   
6572   Larissa Alves              DF                    4    cartao_credito   
6573   Bianca Santos              MA                    5    cartao_credito   

      Quantidade de parcelas  Latitude  Longitude  
0                          2    -13.29     -41.71  
1                          1    -22.19     -48.79  
2                          1    -22.19     -48.79  
3                          1    -22.19     -48.79  
4                          1    -22.19     -48.79  
...                      ...       ...        ...  
6569                       3    -12.64     -55.42  
6570                       3    -22.25     -42.66  
6571                       8    -22.25     -42.66  
6572                       5    -15.83     -47.86  
6573                       4     -5.42     -45.44  

[6574 rows x 13 columns]

In [27]:
df_produtos.to_csv(csv_path + "produtos.csv", index=False)